# Software Entwicklung 

## Kapitel 9: IO

Unter *IO* (Input/Output) versteht man alle Mechanismen,
die mit dem Ausleiten von Daten aus einem Programm
bzw. dem Einlesen von Daten in ein Programm zusammenhängen.

### 9.1 Zeichenkodierung

Möchte ein Programm Daten senden (z.B. in eine Datei
oder über eine Netzwerkverbindung) oder diese empfangen,
werden letztendlich Bytes übertragen. Handelt es sich bei den
Daten um Text - also lesbare Zeichen - so muss durch eine
Zeichenkodierung (engl. *encoding*) festgelegt werden,
wie dieser Text auf Bytes abgebildet wird.

Ein sehr übliches Kodierungsschema ist *UTF-8*. Darin werden
die Zahlen 0 bis 127 analog zum alten ASCII-Standard
insbesondere für grundlegende lateinische Zeichen in
Groß- und Kleinschrift verwendet. Alle übrigen Zeichen wie
z.B. deutsche Umlaute, chinesische Schriftzeichen,
Emojis etc. werden durch größere Zahlen ggf. mit mehreren
Bytes codiert. Die Zuordnung der Zahlen zu den Zeichen
ist durch den [*Unicode*-Standard](http://www.unicode.org/)
festgelegt.

Möchte man eine Python-Zeichenkette in eine Unicode-Bytefolge
übertragen, so kann dafür die Methode <code>encode</code> der Klasse
*str* (String) verwendet werden.

In [ ]:
text = "Nürnberg ist schön"
print(f"Länge {len(text)}")
utf8 = text.encode("utf-8")
print(utf8)
print(f"Länge {len(utf8)}")

Das vorangestellte <code>b</code> signalisiert, dass es sich
hier um eine Bytefolge handelt.

In [ ]:
print(type(utf8))

Eine solche Bytefolge kann auch wieder in einen
Textstring verwandelt werden. Dazu besitzt die
Klasse *bytes* die Methode <code>decode</code>.

In [ ]:
decoded_text = utf8.decode("utf-8")
print(decoded_text)
print(f"Länge {len(decoded_text)}")


### 9.2 Dateien

Unter *Textdateien* verstehen wir Dateien, die
mit einem Texteditor erzeugt und bearbeitet werden können.
Der Inhalt sind lesbare Zeichen, die meist
in Zeilen organisiert sind. Um sie auf einem
Speichermedium abzulegen, müssen die Zeichen
in Bytes konvertiert bzw. beim Lesen
rückübertragen werden.

*Binärdateien* sind Dateien, für die keine Kodierung
stattfinden soll (z.B. Bilder).

Python besitzt bereits im Standard Funktionen, Klassen und Methoden,
die das Lesen und Schreiben von Dateien sowie das Übertragen
von Text in Bytes (und zurück) unterstützen.

Einstiegspunkt ist die Built-In-Funktion <code>open</code>, die ein
Dateiobjekt zurückliefert. Die Parameter von <code>open</code> sind
der *Dateiname* (ggf. inkl. Pfad) und der *Bearbeitungsmodus*
sowie weitere, weniger gebräuchliche optionale Parameter.


| *Bearbeitungsmodus*  | *Bedeutung*                                        |
|:--------------------:|----------------------------------------------------|
| 'r'                  | Die Datei wird gelesen (muss bereits existieren)   |
| 'w'                  | Die Datei wird geschrieben (vorhandene Datei wird überschrieben)   |
| 'a'                  | Die Datei wird geschrieben (neuer Inhalt wird angehängt)   |
| 'r+'                 | Die Datei wird gelesen und geschrieben  |

Standardmäßig finden die Lese- und Schreiboperationen mit der Standard-Kodierung des verwendeten Betriebssystems statt. Soll die Kodierung unterbleiben, muss an den Bearbeitungsmodus ein <code>'b'</code>
(für binär) angehängt werden.

In [ ]:
f = open("091a Textdatei", "r")

Das auf diese Weise erhaltene Dateiobjekt kann für (je nach
Bearbeitungsmodus) für das Lesen und Schreiben benutzt werden.
Die Methode <code>read</code> ohne Angabe eines Parameter
liest den gesamten Inhalt der Datei ein
(Vorsicht: nur bei kleinen Dateien ratsam, da speicherintensiv).

In [ ]:
content = f.read()
print(content)

Jedes geöffnete Dateiobjekt muss auch wieder geschlossen werden,
da andernfalls Betriebssystemressourcen dauerhaft belegt bleiben.

In [ ]:
print(f.closed)
f.close()
print(f.closed)

Sollte eine Textdatei in einer anderen Kodierung als die Standard-Kodierung vorliegen, kann die gewünschte Kodierung mittels des Parameters <code>encoding</code> angegeben werden. Mit <code>encoding=None</code> wird wieder die Standard-Kodierung gewählt, was dem Standardwert und damit dem Weglassen des Parameters entspricht. Im folgenden Beispiel wird eine Textdatei geladen, die im UTF-8-Format vorliegt. Die Standard-Kodierung auf Windows weicht allerdings davon ab, wie man an den Umlauten erkennen kann.

In [ ]:
f = open("utf8_text", "r", encoding=None)
content = f.read()
print(content)
f.close()

### 9.3 Kontextmanager

Die strenge Verpflichtung, jede Datei auch zu schließen, ist
gelegentlich nicht einfach zu erfüllen. Falls z.B. eine
Exception auftritt und die Abarbeitungsreihenfolge
abgebrochen wird, ist trotzdem *close* aufzurufen.

In [ ]:
try:
    f = open("091a Textdatei", "r")
    z = 1 / 0
    # f.close() würde nicht erreicht!
except:
    print("Fehler!")
finally:
    f.close()
print(f.closed)

Python bietet für dieses Problem den *Kontextmanager* an. Er
initialisiert einen *Kontext* für ein Objekt, führt einen
Codeblock in diesem Kontext aus und räumt beim Verlassen
des *Kontext* belegte Ressourcen auf.

Das Schlüsselwort für den Beginn eines *Kontext* ist <code>with</code>.

In [ ]:
with open("091a Textdatei", "r") as f:
    print(f.read())
    print(f.closed)

print(f.closed)

Wie ist das realisiert? Tatsächlich nutzt der
*Kontextmanager* die beiden *dunder*-Methoden
<code>\_\_entry\_\_</code> und <code>\_\_exit\_\_</code>.
Die Methode <code>\_\_entry\_\_</code> wird beim Betreten des
Kontext aufgerufen, die Methode <code>\_\_exit\_\_</code> beim
Verlassen oder beim Auftreten einer nicht behandelten Exception.

Beim Datei-Objekt von Python wird in der
<code>\_\_exit\_\_</code>-Methode sichergestellt, dass die
Datei geschlossen wird.

Durch Überschreiben der Methoden können auch eigene Klassen
sinnvoll mit einem *Kontextmanager* zusammenarbeiten.


